In [6]:
print "Start"
from cStringIO import StringIO
from dl import authClient
from dl import queryClient

import pandas as pd
import datashader as ds
import datashader.glyphs
import datashader.transfer_functions as tf
import bokeh.plotting as bp
from datashader.bokeh_ext import InteractiveImage

# Get the security token for the datalab demo user
token = authClient.login('anonymous')
print "Got token",token

Start
Got token anonymous.0.0.anon_access


In [7]:
depth = 1                    # minimum depth 
raname = 'ra'
decname = 'dec'
mags = 'gmag,rmag'
dbase='smash_dr1.object'

# Create the query string.
query = ('select '+raname+','+decname+','+mags+',sharp,chi,prob from '+dbase+ \
        ' where (depthflag > %d and ' + \
        ' (gmag is not null) and ' + \
        ' (fieldid>55 and fieldid<90))') % \
           (depth)
        
print "Your query is:", query
print "Making query"

# Call the Query Manager Service    
response = queryClient.query(token, adql = query, fmt = 'csv')
df = pd.read_csv(StringIO(response))

print len(df), "objects found."

Your query is: select ra,dec,gmag,rmag,sharp,chi,prob from smash_dr1.object where (depthflag > 1 and  (gmag is not null) and  (fieldid>55 and fieldid<90))
Making query
21073716 objects found.


In [11]:
sharpthresh=1.0
df["Class"]='Star'
df.loc[(abs(df["sharp"])>sharpthresh),"Class"]='Galaxy'
#df.loc[(abs(df["sharp"])>sharpthresh) & (df["prob"]<0.2),"Class"]='Galaxy'
#df.loc[abs(df["chi"])>sharpthresh,"Class"]='Galaxy'
df["Class"]=df["Class"].astype('category')
df["g_r"]=df["gmag"]-df["rmag"]
df.tail()

ra        dec     gmag   rmag  sharp    chi   prob   Class  \
21073711  106.799971 -54.211810  24.2398  99.99 -4.000  1.304  99.99  Galaxy   
21073712  106.807695 -54.208438  99.9900  99.99 -1.691  0.991  99.99  Galaxy   
21073713  106.808112 -54.207899  99.9900  99.99 -2.873  1.091  99.99  Galaxy   
21073714  106.804477 -54.206826  99.9900  99.99 -2.771  1.011  99.99  Galaxy   
21073715  106.798934 -54.209826  24.6338  99.99 -5.833  1.011  99.99  Galaxy   

              g_r  
21073711 -75.7502  
21073712   0.0000  
21073713   0.0000  
21073714   0.0000  
21073715 -75.3562

In [13]:
bp.output_notebook()
p = bp.figure(tools='pan,wheel_zoom,box_zoom,reset',x_range=(14,26), y_range=(0,5))

def image_callback(x_range, y_range, w, h):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'gmag', 'chi', ds.count_cat('Class'))
    img = tf.shade(agg, how='log')
    return tf.dynspread(img, how='add',threshold=0.5)

InteractiveImage(p, image_callback)

Loading BokehJS ...

In [14]:
p = bp.figure(tools='pan,wheel_zoom,box_zoom,reset',x_range=(-2,3), y_range=(14,26))

def image_callback(x_range, y_range, w, h):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'g_r', 'gmag', ds.count_cat('Class'))
    img = tf.shade(agg, how='log')
    return tf.dynspread(img, how='add',threshold=0.5)

InteractiveImage(p, image_callback)